<module 'skimage' from 'C:\\Users\\Samantha\\Anaconda3\\lib\\site-packages\\skimage\\__init__.py'>

In [379]:
import numpy as np

import skimage.io as skio

import skimage.transform
from matplotlib import pyplot as plt

import warnings
warnings.filterwarnings('ignore')

ImportError: cannot import name '_hough_circle'

In [371]:

def align(image1, image2):
    #aligns image 1 to image 2
    offsets = {}
    normalized1 = crop(image1/np.linalg.norm(image1))
    normalized2 = crop(image2/np.linalg.norm(image2))
    flattened2 = np.reshape(normalized2, (-1, 1))
    for i in range(-15, 15):
        rolled_i = np.roll(normalized1, i, axis =0)
        for j in range(-15, 15):
            rolled_j = np.roll(rolled_i, j, axis = 1)
            rolled_j = np.reshape(rolled_j, (1, -1))
            cc = np.dot(rolled_j, flattened2)
            offsets[(i, j)] = cc   
    best_offset = max(offsets, key=offsets.get) 
    return best_offset

In [372]:
def crop_border(image, threshold):
    #attempt at automatic border detection
    to_delete = []
    i = 0
    for row in image:
        if i >= threshold:
            break
        if (sum(row) < 100) or (sum(row)>350):
            to_delete.append(i)
        i+=1
    for index in to_delete:
        np.delete(image, index, 0)
    transpose = image.T
    
    to_delete2 = []
    j = 0
    for row in transpose:
        if j >= threshold:
            break
        if (sum(row) < 100) or (sum(row)>350):
            to_delete2.append(j)
        j+=1
    for index in to_delete2:
        np.delete(transpose, index, 1)
        
    cropped = transpose.T
    return cropped
    

In [373]:
def crop(image):
    image = image[:]
    image = image.T
    image = image[:]
    image = image.T
    return image
    

In [374]:
def align_big(input1, input2, calls):
    #uses successively scaled down versions of the image to do a binary-search-like alignment of image1 to image2
    #returns the shifts of the alignments
    #base case
    print("starting layer ", calls)
    image1 = input1
    image2 = input2
    
    if calls==0:
        transformation = align(image1, image2)
        return transformation
    
    shape = input1.shape
    shape = tuple(s//2 for s in shape)
    downsampled1 = skimage.transform.rescale(image1, 0.5) #downsampled by 1/2 using imresize 
    downsampled2 = skimage.transform.rescale(image2, 0.5) #downsampled
    
    transformation = align_big(downsampled1, downsampled2, calls-1)
    transformation = transformation*2 #have to multiply transformation by 2 because the image is now twice as big

    image1 = np.roll(image1, transformation[0], axis = 0)
    image1 = np.roll(image1, transformation[1], axis = 1)
    
    transformation += align(image1, image2)
    print("finished layer ", calls)
    return transformation

In [375]:
#crop to largest power of two available
import math
def crop_to_power_of_2(image):
    shape = list(image.shape)

    biggest_power = min(2**(math.log(shape[1])//math.log(2)), 2**(math.log(shape[0])//math.log(2)))
    rows_to_crop = (int)(shape[0] - biggest_power)//2
    cols_to_crop = (int)(shape[1] - biggest_power)//2
    if shape[0]%2==1:
        image = image[rows_to_crop:-(rows_to_crop+1)]
    else:
        image = image[rows_to_crop:-(rows_to_crop)]
    
    image = image.T
    if shape[1]%2==1:
        image = image[cols_to_crop:-(cols_to_crop+1)]
    else:
        image = image[cols_to_crop:-(cols_to_crop)]
    image = image.T
    return image

In [376]:
def load(imname):
    # read in the image
    im = skio.imread(imname)
    

    # convert to double (might want to do this later on to save memory)    
    im = sk.img_as_float(im)

    # compute the height of each part (just 1/3 of total)
    height = np.floor(im.shape[0] / 3.0).astype(np.int)

    # separate color channels
    b = im[:height]
    g = im[height: 2*height]
    r = im[2*height: 3*height]
    
    cropped_r = r#crop_to_power_of_2(r)
    cropped_g = g#crop_to_power_of_2(g)
    cropped_b = b#crop_to_power_of_2(b)
    
    ar = align_big(cropped_r, cropped_b, 10)
    aligned_red = np.roll(r, ar[0], axis = 0)
    aligned_red = np.roll(aligned_red, ar[1], axis = 1)
    
    ag = align_big(cropped_g, cropped_b, 10)
    aligned_green = np.roll(g, ag[0], axis = 0)
    aligned_green = np.roll(aligned_green, ag[1], axis = 1)
    
    im_out = np.dstack([aligned_red, aligned_green, b])
    skio.imshow(im_out)
    plt.show()

In [377]:

load('harvesters.tif')

starting layer  10


AttributeError: module 'skimage' has no attribute 'transform'

In [241]:
#theories as to why it doesnt work:
#off by one errors due to floor division add up as the powers of two get larger


(128, 128)

In [206]:
im = skio.imread('harvesters.tif')
im.shape
2**(math.log(im.shape[1])//math.log(2))


2048.0